# ทดสอบการค้นคืนข่าวที่น่าชื่อถือจากทุกแหล่ง (cofact/anti/sure) ด้วย cosine similarity + TF-IDF (ใช้เฉพาะหัวข้อข่าว(header จาก cofact_refer + anti_info + sure_info.json) 10/12/2021)

In [1]:
import numpy as np
import nltk
import re
import pandas as pd 
import json
import os
import pickle
import csv

from pythainlp import word_tokenize
from pythainlp.corpus import thai_stopwords
from nltk.stem.porter import PorterStemmer
from nltk.corpus import words
from stop_words import get_stop_words
from string import punctuation

from sklearn.preprocessing import normalize
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from scipy import spatial

from ast import literal_eval

from urllib.parse import urlparse

nltk.download('words')
th_stop = thai_stopwords()
en_stop = get_stop_words('en')
p_stemmer = PorterStemmer()

def split_word(text):
    tokens = word_tokenize(text,engine='newmm')
    
    # Remove stop words ภาษาไทย และอักขระพิเศษ
    tokens = [i for i in tokens if (not i in th_stop) & (not i in en_stop) & (not i in punctuation) & (not i in ["'",'"','“','”','‘','’','\n',"None", ' '])] 
    
    # ลบตัวเลข
    tokens = [i for i in tokens if not i.isnumeric()]
    
    # ลบช่องว่าง
    tokens = [i for i in tokens if not ' ' in i]

    return tokens

def remove_emojis(data):
    emoj = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)
    return re.sub(emoj, '', data)

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\Administrator\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


## ดึงข้อมูลของ cofact

In [2]:
def read_cofact_refer(): #สำหรับดึงข้อมูลของ cofact csv
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../result/Cofact/cofact_refer.csv')
    
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)

    # read header from CSV file
    header = []
    header = next(csvreader)
    
    rows = []
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        
        # เพิ่ม header
        tmp.append(row[1]) 

        # เพิ่ม content
        # content_parts = literal_eval(row[2])
        # content = ''.join(filter(None, content_parts))
        
        tmp.append(row[2])
        
        # เพิ่ม link (ข่าวต้นทางสุด)
        tmp.append(row[3])
        
        # เพิ่ม datetime
        if (len(row) == 7):
            tmp.append(row[6])
        else:
            tmp.append("")
        
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [3]:
cofact_refer_text_list = read_cofact_refer()

In [4]:
cofact_refer_text_list

[['กรมอนามัย เตือนซดน้ำอัดลมดับร้อน เสี่ยงฟันผุ อ้วนฉุ แนะดื่มน้ำเปล่า',
  'กรมอนามัย กระทรวงสาธารณสุข เตือนคนไทยดื่มน้ำอัดลมมาก จะส่งผลต่อสุขภาพช่องปาก เกิดโรคฟันผุและโรคอ้วนได้ แนะควรดื่มน้ำเปล่า 8 แก้ว เพื่อสร้างความสดชื่นให้กับร่างกายดร.นพ.พรเทพ ศิริวนารังสรรค์ อธิบดีกรมอนามัย กล่าวว่า ขณะนี้ได้เข้าสู่ฤดูร้อน จึงทำให้รู้สึกกระหายน้ำการดื่มเครื่องดื่มที่มีรสหวาน หรือ น้ำอัดลม จึงเป็นทางเลือกลำดับต้นๆ ทั้งๆ ที่ เครื่องดื่มที่ดีและเหมาะสมกับร่างกาย คือ น้ำเปล่า เพราะในน้ำเปล่า มีส่วนช่วยให้ร่างกายสดชื่น เพิ่มการไหลเวียนของโลหิต ปรับสมดุลของร่างกาย ช่วยชะลอความแก่ เพิ่มความชุ่มชื่นแก่ผิว ช่วยให้ระบบย่อยในกระเพาะอาหารทำงานได้ดีขึ้น ช่วยขับถ่ายของเสียออกจากร่างกาย ไตแข็งแรง โดย 1 วันควรดื่มน้ำสะอาดอย่างน้อยวันละ 8 แก้ว ในทางตรงกันข้ามหากเลือกดื่มน้ำหวานหรือน้ำอัดลมแทนน้ำเปล่าจะส่งผลเสียแก่ร่างกาย ได้แก่ โรคฟันผุ โรคอ้วน โรคกระดูกพรุน กระดูกเปราะ เนื่องจากน้ำหวานชนิดอัดลมมีกรดคาร์บอนิกค่อนข้างมาก ซึ่งสารดังกล่าวจะกีดขวางการดูดซึมแคลเซียมของกระดูก การดื่มน้ำอัดลมเป็นประจำเป็นอีกหนึ่งสาเหตุ

In [5]:
len(cofact_refer_text_list)

1163

-----------------------------------------------
## ดึงข้อมูลของ anti

In [6]:
def read_anti_refer(): #สำหรับดึงข้อมูลของ anti fake news csv
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../result/Anti/anti_info.csv')
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)
    
    # read header from CSV file
    header = []
    header = next(csvreader)

    rows = []
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        
        # เพิ่ม header
        tmp.append(row[1])
        
        # เพิ่ม content
        content_parts = literal_eval(row[2])
        content = ''.join(filter(None, content_parts))
        tmp.append(content)
        
        # เพิ่ม link
        tmp.append(row[3])
        
        # เพิ่ม datetime
        tmp.append(row[5])
        
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [7]:
anti_refer_text_list = read_anti_refer()

In [8]:
anti_refer_text_list

[['อย่าหลงเชื่อ ข่าวปลอม ยาพาราเซตามอลปนเปื้อนเชื้อไวรัส',
  'เป็นกระแสดังมาก ถึงเรื่องการห้ามกินยาพาราเซตามอล ที่เขียนว่า P-500 บนแผง เพราะมีไวรัสมาชูโปปนเปื้อนในยาพาราเซตามอล แบบ 500 mg ซึ่งมีอันตรายถึงตาย\nซึ่งข่าวนี้ อย. เช็คแล้ว ไม่เป็นความจริงสำนักงานคณะกรรมการอาหารและยา (อย.) ได้ตรวจสอบพบว่า ภาพแผงยาที่ถูกแชร์นั้นเป็นยาที่ผลิตจากประเทศอินเดีย ยืนยันว่าไม่ได้ขึ้นทะเบียนที่ประเทศไทยและไม่มีวางขายที่ประเทศไทยแน่นอน อีกประเด็นคือ เชื้อมาชูโปไวรัส เป็นเชื้อที่ไม่สามารถเจริญเติบโตในที่แห้ง การที่จะปนเปื้อนเชื้อดังกล่าวในยาพาราเซตามอลนั้นจึงมีความเป็นไปได้น้อยมากดังนั้น ในประเทศไทย ผู้บริโภคจึงมั่นใจได้ว่า สามารถรับประทานยาพาราเซตามอลได้ตามปกติอย่างไรก็ตาม การผลิตยาในประเทศไทยต้องใช้หลักเกณฑ์และวิธีการที่ดีในการผลิตยา (GMP) ในการควบคุมคุณภาพและมาตรฐาน และมีการกำกับดูแลทั้งก่อนออกสู่ตลาดและหลังออกสู่ตลาดแต่หากพบว่ายาใดมีการปนเปื้อนของสารอันตราย ไม่ปลอดภัยในการใช้ อย.จะเรียกเก็บยาคืน และแจ้งเตือนให้ผู้บริโภคทราบโดยเร็ว\nมีสติก่อนแชร์ อย่าหลงเชื่อแหล่งข่าวที่ไม่น่าเชื่อถือ ตรวจสอบเช็คให้ช

In [9]:
len(anti_refer_text_list)

2656

-----------------------------------------------
## ดึงข้อมูลของ sure

In [10]:
def read_sure_refer(): #สำหรับดึงข้อมูลของ sure and share csv
    # Opening CSV file
    root_path = os.getcwd()
    path = os.path.join(root_path, '../result/Sure/sure_info.csv')
    f = open(path, encoding="utf8")
    
    # returns CSV object as
    # a dictionary
    csvreader = csv.reader(f)
    
    # read header from CSV file
    header = []
    header = next(csvreader)

    rows = []
    for row in csvreader:
        tmp = []
        
        content_parts = []
        content = ''
        
        # เพิ่ม header
        tmp.append(row[1])
        
        # เพิ่ม content
        content_parts = literal_eval(row[2])
        content = ''.join(filter(None, content_parts))
        tmp.append(content)
        
        # เพิ่ม link
        tmp.append(row[3])
        
        # เพิ่ม datetime
        tmp.append(row[5])
        
        rows.append(tmp)

    # Closing file
    f.close()
    
    return rows

In [11]:
sure_refer_text_list = read_sure_refer()

In [12]:
sure_refer_text_list

[['ชัวร์ก่อนแชร์ : เทคนิคซักผ้าด้วยเครื่องไม่ทำให้ผ้าพันกัน จริงหรือ?',
  'กทม. 14 เม.ย.-บนสังคมออนไลน์แชร์คลิปเทคนิคการซักผ้าด้วยเครื่องให้ไม่พันกัน เรื่องนี้จริงหรือไม่ ติดตามจากศูนย์ชัวร์ก่อนแชร์.-สำนักข่าวไทย',
  'https://tna.mcot.net/tna-101176',
  '01/01/2513 00:00'],
 ['ชัวร์ก่อนแชร์ : ยาแอสไพรินช่วยซักผ้าขาวสะอาด จริงหรือ?',
  'กทม. 12 เม.ย.-บนสังคมออนไลน์แชร์แนะนำเคล็ดลับซักผ้าขาวด้วยการใส่ยาแอสไพรินลงไปจะช่วยขจัดคราบขจัดกลิ่นได้ เรื่องนี้จริงหรือไม่ ติดตามจากศูนย์ชัวร์ก่อนแชร์.-สำนักข่าวไทยบทสรุป : ไม่จริง ไม่ควรแชร์ศูนย์ชัวร์ก่อนแชร์ สำนักข่าวไทย ตรวจสอบกับ ผศ.ภก.ดร.บดินทร์ ติวสุวรรณ คณะเภสัชศาสตร์ จุฬาฯ ได้รับการยืนยันว่าไม่เป็นความจริง แอสไพรินไม่มีคุณสมบัติในการซักล้าง เพราะละลายน้ำไม่ค่อยดี เป็นเพียงยาลดการอักเสบใช้ต้านการเกาะกลุ่มของเกร็ดเลือด แม้จะเสื่อมสภาพแล้วและมีความเป็นกรด แต่คุณสมบัติดังกล่าวไม่สามารถทำให้ผ้าสะอาดได้จากการทดลองนำแอสไพรินมาบดละลายน้ำ พบว่าละลายได้ไม่ดี จึงเป็นไปได้ยากที่จะทำให้เสื้อผ้าสะอาด ผิดกับผ้าที่แช่ผงซักฟอกจะกำจัดคราบสกปรกได้ดีกว่า เนื่องจา

In [13]:
len(sure_refer_text_list)

1839

## รวมทุก list จากทุกแหล่งข่าวเข้าด้วยกัน

In [14]:
cofact_refer_text_list[:2]

[['กรมอนามัย เตือนซดน้ำอัดลมดับร้อน เสี่ยงฟันผุ อ้วนฉุ แนะดื่มน้ำเปล่า',
  'กรมอนามัย กระทรวงสาธารณสุข เตือนคนไทยดื่มน้ำอัดลมมาก จะส่งผลต่อสุขภาพช่องปาก เกิดโรคฟันผุและโรคอ้วนได้ แนะควรดื่มน้ำเปล่า 8 แก้ว เพื่อสร้างความสดชื่นให้กับร่างกายดร.นพ.พรเทพ ศิริวนารังสรรค์ อธิบดีกรมอนามัย กล่าวว่า ขณะนี้ได้เข้าสู่ฤดูร้อน จึงทำให้รู้สึกกระหายน้ำการดื่มเครื่องดื่มที่มีรสหวาน หรือ น้ำอัดลม จึงเป็นทางเลือกลำดับต้นๆ ทั้งๆ ที่ เครื่องดื่มที่ดีและเหมาะสมกับร่างกาย คือ น้ำเปล่า เพราะในน้ำเปล่า มีส่วนช่วยให้ร่างกายสดชื่น เพิ่มการไหลเวียนของโลหิต ปรับสมดุลของร่างกาย ช่วยชะลอความแก่ เพิ่มความชุ่มชื่นแก่ผิว ช่วยให้ระบบย่อยในกระเพาะอาหารทำงานได้ดีขึ้น ช่วยขับถ่ายของเสียออกจากร่างกาย ไตแข็งแรง โดย 1 วันควรดื่มน้ำสะอาดอย่างน้อยวันละ 8 แก้ว ในทางตรงกันข้ามหากเลือกดื่มน้ำหวานหรือน้ำอัดลมแทนน้ำเปล่าจะส่งผลเสียแก่ร่างกาย ได้แก่ โรคฟันผุ โรคอ้วน โรคกระดูกพรุน กระดูกเปราะ เนื่องจากน้ำหวานชนิดอัดลมมีกรดคาร์บอนิกค่อนข้างมาก ซึ่งสารดังกล่าวจะกีดขวางการดูดซึมแคลเซียมของกระดูก การดื่มน้ำอัดลมเป็นประจำเป็นอีกหนึ่งสาเหตุ

In [15]:
anti_refer_text_list[:2]

[['อย่าหลงเชื่อ ข่าวปลอม ยาพาราเซตามอลปนเปื้อนเชื้อไวรัส',
  'เป็นกระแสดังมาก ถึงเรื่องการห้ามกินยาพาราเซตามอล ที่เขียนว่า P-500 บนแผง เพราะมีไวรัสมาชูโปปนเปื้อนในยาพาราเซตามอล แบบ 500 mg ซึ่งมีอันตรายถึงตาย\nซึ่งข่าวนี้ อย. เช็คแล้ว ไม่เป็นความจริงสำนักงานคณะกรรมการอาหารและยา (อย.) ได้ตรวจสอบพบว่า ภาพแผงยาที่ถูกแชร์นั้นเป็นยาที่ผลิตจากประเทศอินเดีย ยืนยันว่าไม่ได้ขึ้นทะเบียนที่ประเทศไทยและไม่มีวางขายที่ประเทศไทยแน่นอน อีกประเด็นคือ เชื้อมาชูโปไวรัส เป็นเชื้อที่ไม่สามารถเจริญเติบโตในที่แห้ง การที่จะปนเปื้อนเชื้อดังกล่าวในยาพาราเซตามอลนั้นจึงมีความเป็นไปได้น้อยมากดังนั้น ในประเทศไทย ผู้บริโภคจึงมั่นใจได้ว่า สามารถรับประทานยาพาราเซตามอลได้ตามปกติอย่างไรก็ตาม การผลิตยาในประเทศไทยต้องใช้หลักเกณฑ์และวิธีการที่ดีในการผลิตยา (GMP) ในการควบคุมคุณภาพและมาตรฐาน และมีการกำกับดูแลทั้งก่อนออกสู่ตลาดและหลังออกสู่ตลาดแต่หากพบว่ายาใดมีการปนเปื้อนของสารอันตราย ไม่ปลอดภัยในการใช้ อย.จะเรียกเก็บยาคืน และแจ้งเตือนให้ผู้บริโภคทราบโดยเร็ว\nมีสติก่อนแชร์ อย่าหลงเชื่อแหล่งข่าวที่ไม่น่าเชื่อถือ ตรวจสอบเช็คให้ช

In [16]:
sure_refer_text_list[:2]

[['ชัวร์ก่อนแชร์ : เทคนิคซักผ้าด้วยเครื่องไม่ทำให้ผ้าพันกัน จริงหรือ?',
  'กทม. 14 เม.ย.-บนสังคมออนไลน์แชร์คลิปเทคนิคการซักผ้าด้วยเครื่องให้ไม่พันกัน เรื่องนี้จริงหรือไม่ ติดตามจากศูนย์ชัวร์ก่อนแชร์.-สำนักข่าวไทย',
  'https://tna.mcot.net/tna-101176',
  '01/01/2513 00:00'],
 ['ชัวร์ก่อนแชร์ : ยาแอสไพรินช่วยซักผ้าขาวสะอาด จริงหรือ?',
  'กทม. 12 เม.ย.-บนสังคมออนไลน์แชร์แนะนำเคล็ดลับซักผ้าขาวด้วยการใส่ยาแอสไพรินลงไปจะช่วยขจัดคราบขจัดกลิ่นได้ เรื่องนี้จริงหรือไม่ ติดตามจากศูนย์ชัวร์ก่อนแชร์.-สำนักข่าวไทยบทสรุป : ไม่จริง ไม่ควรแชร์ศูนย์ชัวร์ก่อนแชร์ สำนักข่าวไทย ตรวจสอบกับ ผศ.ภก.ดร.บดินทร์ ติวสุวรรณ คณะเภสัชศาสตร์ จุฬาฯ ได้รับการยืนยันว่าไม่เป็นความจริง แอสไพรินไม่มีคุณสมบัติในการซักล้าง เพราะละลายน้ำไม่ค่อยดี เป็นเพียงยาลดการอักเสบใช้ต้านการเกาะกลุ่มของเกร็ดเลือด แม้จะเสื่อมสภาพแล้วและมีความเป็นกรด แต่คุณสมบัติดังกล่าวไม่สามารถทำให้ผ้าสะอาดได้จากการทดลองนำแอสไพรินมาบดละลายน้ำ พบว่าละลายได้ไม่ดี จึงเป็นไปได้ยากที่จะทำให้เสื้อผ้าสะอาด ผิดกับผ้าที่แช่ผงซักฟอกจะกำจัดคราบสกปรกได้ดีกว่า เนื่องจา

In [17]:
all_refer_text_list = []
all_refer_text_list = cofact_refer_text_list + anti_refer_text_list + sure_refer_text_list

In [18]:
all_refer_text_list

[['กรมอนามัย เตือนซดน้ำอัดลมดับร้อน เสี่ยงฟันผุ อ้วนฉุ แนะดื่มน้ำเปล่า',
  'กรมอนามัย กระทรวงสาธารณสุข เตือนคนไทยดื่มน้ำอัดลมมาก จะส่งผลต่อสุขภาพช่องปาก เกิดโรคฟันผุและโรคอ้วนได้ แนะควรดื่มน้ำเปล่า 8 แก้ว เพื่อสร้างความสดชื่นให้กับร่างกายดร.นพ.พรเทพ ศิริวนารังสรรค์ อธิบดีกรมอนามัย กล่าวว่า ขณะนี้ได้เข้าสู่ฤดูร้อน จึงทำให้รู้สึกกระหายน้ำการดื่มเครื่องดื่มที่มีรสหวาน หรือ น้ำอัดลม จึงเป็นทางเลือกลำดับต้นๆ ทั้งๆ ที่ เครื่องดื่มที่ดีและเหมาะสมกับร่างกาย คือ น้ำเปล่า เพราะในน้ำเปล่า มีส่วนช่วยให้ร่างกายสดชื่น เพิ่มการไหลเวียนของโลหิต ปรับสมดุลของร่างกาย ช่วยชะลอความแก่ เพิ่มความชุ่มชื่นแก่ผิว ช่วยให้ระบบย่อยในกระเพาะอาหารทำงานได้ดีขึ้น ช่วยขับถ่ายของเสียออกจากร่างกาย ไตแข็งแรง โดย 1 วันควรดื่มน้ำสะอาดอย่างน้อยวันละ 8 แก้ว ในทางตรงกันข้ามหากเลือกดื่มน้ำหวานหรือน้ำอัดลมแทนน้ำเปล่าจะส่งผลเสียแก่ร่างกาย ได้แก่ โรคฟันผุ โรคอ้วน โรคกระดูกพรุน กระดูกเปราะ เนื่องจากน้ำหวานชนิดอัดลมมีกรดคาร์บอนิกค่อนข้างมาก ซึ่งสารดังกล่าวจะกีดขวางการดูดซึมแคลเซียมของกระดูก การดื่มน้ำอัดลมเป็นประจำเป็นอีกหนึ่งสาเหตุ

In [19]:
len(all_refer_text_list)

5658

## ------------------------------------------------------------------------------
## สร้าง dataframe ของทุกแหล่งข่าวสำหรับอ้างถึงตอนแนบลิงค์ url แสดงผล

In [20]:
all_refer_header = []
all_refer_content = []
all_refer_url = []
all_refer_datetime = []
all_refer_domain = []

for i in range(len(all_refer_text_list)):
    all_refer_header.append(all_refer_text_list[i][0]) #list ของส่วนหัวข้อข่าว
    all_refer_content.append(all_refer_text_list[i][1]) #list ของส่วนเนื้อหาเท่านั้น
    all_refer_url.append(all_refer_text_list[i][2]) #list ของ url เท่านั้น
    all_refer_datetime.append(all_refer_text_list[i][3]) #list ของ datetime เท่านั้น
    all_refer_domain.append(urlparse(all_refer_text_list[i][2]).hostname) #list ของ domain เท่านั้น


In [21]:
#ทำ list ให้เป็น dataframe
all_original_text_and_headline_news_df = pd.DataFrame(list(zip(all_refer_header, all_refer_content, all_refer_url, all_refer_datetime, all_refer_domain)), columns=["หัวข้อข่าวอ้างอิงของ ทุกแหล่งข่าว", "เนื้อหาข่าวอ้างอิงของ ทุกแหล่งข่าว", "URL ของ ทุกแหล่งข่าว", "เวลาที่เผยแพร่ข่าวของ ทุกแหล่งข่าว", "domain เจ้าของข่าว ทุกแหล่งข่าว" ])

all_original_text_and_headline_news_df

หัวข้อข่าวอ้างอิงของ ทุกแหล่งข่าว  \
0     กรมอนามัย เตือนซดน้ำอัดลมดับร้อน เสี่ยงฟันผุ อ...   
1                              7 อาหาร อัปไซส์ให้อกอึ๋ม   
2         อย่าแชร์ ยาสีฟันรักษาสิวอักเสบ สธ.ยันทำไม่ได้   
3     ธปท.สอบเคส "สาวแบงก์" ลาออกหลังโดนบังคับขายประ...   
4     แบงก์ชาติเตือนภัย SMS “คุณได้รับสินเชื่อจาก ธป...   
...                                                 ...   
5653  ชัวร์ก่อนแชร์: Harvard เผยชุมชนที่ฉีดวัคซีนมาก...   
5654  ชัวร์ก่อนแชร์: เด็กมีโอกาสเสียชีวิตจากวัคซีนมา...   
5655  ชัวร์ก่อนแชร์: ทารกเสียชีวิตจากนมแม่ปนเปื้อนโป...   
5656  ชัวร์ก่อนแชร์: โนวัค ยอโควิช คือนักฬาคนแรกที่ถ...   
5657  ชัวร์ก่อนแชร์: หลังฉีดวัคซีนเข็มกระตุ้น 3 เดือ...   

                     เนื้อหาข่าวอ้างอิงของ ทุกแหล่งข่าว  \
0     กรมอนามัย กระทรวงสาธารณสุข เตือนคนไทยดื่มน้ำอั...   
1     ใครๆ ก็อยากดูมีสรีระดีทุกวัดส่วน โดยเฉพาะอย่าง...   
2     กระทรวงสาธารณสุขยืนยันยาสีฟันรักษาสิวไม่ได้ แม...   
3     ธปท.เร่งสอบเคสสาวแบงก์โพสต์ลาออกจากพนักงาน หลั...   
4     โปรดฟังอีกครั้งหนึ่ง ธนาคารแห่งประเทศไทยประกาศ...   
...                                                 ...   
5653  01 กุมภาพันธ์ 2565ตรวจสอบข้อเท็จจริงโดย: Polit...   
5654  02 กุมภาพันธ์ 2565ตรวจสอบข้อเท็จจริงโดย: Polit...   
5655  04 กุมภาพันธ์ 2565ตรวจสอบข้อเท็จจริงโดย: Polit...   
5656  07 กุมภาพันธ์ 2565ตรวจสอบข้อเท็จจริงโดย: Polit...   
5657  07 กุมภาพันธ์ 2565ตรวจสอบข้อเท็จจริงโดย: Vox C...   

                                   URL ของ ทุกแหล่งข่าว  \
0        https://mgronline.com/qol/detail/9580000042071   
1     https://mgronline.com/goodhealth/detail/960000...   
2     https://mgronline.com/onlinesection/detail/963...   
3             https://news.thaipbs.or.th/content/309834   
4     https://mgronline.com/onlinesection/detail/964...   
...                                                 ...   
5653            https://tna.mcot.net/latest-news-874316   
5654            https://tna.mcot.net/latest-news-875216   
5655            https://tna.mcot.net/latest-news-876634   
5656            https://tna.mcot.net/latest-news-877540   
5657            https://tna.mcot.net/latest-news-878300   

     เวลาที่เผยแพร่ข่าวของ ทุกแหล่งข่าว domain เจ้าของข่าว ทุกแหล่งข่าว  
0                   12 เม.ย. 2558 22:13                   mgronline.com  
1                    1 มิ.ย. 2560 11:44                   mgronline.com  
2                   11 มี.ค. 2563 22:55                   mgronline.com  
3                  11:20 | 18 พฤศจิกายน              news.thaipbs.or.th  
4                    29 ก.ย. 2564 06:42                   mgronline.com  
...                                 ...                             ...  
5653                   01/02/2565 18:54                    tna.mcot.net  
5654                   02/02/2565 21:46                    tna.mcot.net  
5655                   04/02/2565 16:26                    tna.mcot.net  
5656                   07/02/2565 05:56                    tna.mcot.net  
5657                   07/02/2565 21:01                    tna.mcot.net  

[5658 rows x 5 columns]

In [22]:
all_headline_tokens_list = [split_word(txt) for txt in all_refer_header] #นำ list ของหังข้อข่าวมาตัดคำ

In [23]:
all_tokens_list_j = [','.join(tkn) for tkn in all_headline_tokens_list]

----------------------------------------------------------------------------------
# สร้าง vocabulary set

In [24]:
print(all_tokens_list_j[0].split(",")[0:2])


['กรมอนามัย', 'เตือน']


In [25]:
## Create Vocabulary
tokens_list = []

for words in all_tokens_list_j:
    # print(words)
    temp_list = words.split(",")
    # print(temp_list)
    for i in temp_list:
        tokens_list.append(i)

vocabulary = set(tokens_list)
vocabulary = list(vocabulary)

In [26]:
len(vocabulary)

6711

--------------------------------------------------------------------------------------

In [27]:
tvec = TfidfVectorizer(analyzer=lambda x:x.split(','),)
original_c_feat = tvec.fit_transform(all_tokens_list_j)

### Save Trained TFID Model

In [28]:
### Save model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
with open(path,'wb') as handle:
    pickle.dump(original_c_feat, handle)

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


In [29]:
### load model
root_path = os.getcwd()
path = os.path.join(root_path, 'all-tfid.pkl')
print(path)
t = pickle.load(open(path,'rb'))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\all-tfid.pkl


### Save Vocabulary

In [30]:
### Save Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "w", encoding="utf-8") as file:
    file.write(str(vocabulary))

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [31]:
### load Vacabulary
root_path = os.getcwd()
path = os.path.join(root_path, 'vocabulary_all.txt')
print(path)
with open(path, "r", encoding="utf-8") as file:
    data2 = eval(file.readline())

c:\Users\Administrator\Documents\SeniorProject\Senior-project\Preprocess\vocabulary_all.txt


In [32]:
data2

['',
 'วางยา',
 'ถั่ว',
 'มั่ว',
 'ไบคาร์บอเนต',
 'ลึกลับ',
 'เพศ',
 'ตะขาบ',
 'โรลออน',
 'ตามกฎหมาย',
 'ปลอม',
 'รุ้ง',
 'ทะลาย',
 'กานพลู',
 'จับตา',
 'การเมือง',
 'ทดลอง',
 'เทียบ',
 'ก่อ',
 'มีเงิน',
 'สบู่',
 'กัตซัย',
 'ซื้อ',
 'U',
 'จักจั่น',
 'เป็นปัญหา',
 'ทางม้าลาย',
 'เวลาเปิด',
 'ท้องเสีย',
 'ข้อเสีย',
 'ฐานราก',
 'ผู้ประกันตน',
 'โอเมก้า',
 'ท.',
 'ขนมหวาน',
 'กันชน',
 'ผู้โดยสาร',
 'การตาย',
 'ถั่ง',
 'ฯลด',
 'เครื่องบิน',
 'ยุค',
 'ข้อดี',
 'EXPERT',
 'รับงาน',
 'โปแลนด์',
 'เครื่องซักผ้า',
 'Hub',
 'นักบิน',
 'หยาง',
 'โรคสมอง',
 'ผลผลิต',
 'อลฟิน',
 'Virus',
 'จิก',
 'ทำผิด',
 'ล.',
 '“ช',
 'มิสเตอร์',
 'เป็นอันตราย',
 'ตรัส',
 'ห้าม',
 'ผู้สูงอายุ',
 'การแสดงออก',
 'เวลา',
 'คำโฆษณา',
 'เผยแพร่',
 'รับจ้าง',
 'แม้ว',
 'ห้าง',
 '35',
 'หูฟัง',
 'เครื่องดื่ม',
 'นักวิจัย',
 'ลบ',
 'สต',
 'แมงกะพรุน',
 'ดักแด้',
 'ดาราศาสตร์',
 'สบู่เหลว',
 'นครปฐม',
 'ศาสนาประจำชาติ',
 'โดยสาร',
 'สิวเสี้ยน',
 'ภัย',
 'ยุง',
 'คาดการณ์',
 'กรกฎาคม',
 'รู้เท่าทัน',
 'เซียล',
 'บิ',
 'ไอ

In [33]:
len(data2)

6711

## Create vector for Query/search keywords

In [34]:
## Create vector for Query/search keywords
def gen_vector_T(tokens):

    Q = np.zeros((len(vocabulary)))
    
    x = tvec.transform(tokens)
    
    x = x.A[0]
    return x

### Calculate Cosine similarity of trained Tfidf to input query


In [35]:
norm_original_c_feat = normalize(original_c_feat)
norm_original_c_feat = norm_original_c_feat.toarray()
norm_original_c_feat = norm_original_c_feat.T

In [36]:
query_vector = []
def cosine_similarity_T(k, query):
    tokens = split_word(str(query))
    q_df = pd.DataFrame(columns=['q_clean'])
    q_df.loc[0,'q_clean'] =str(tokens)

    q_df=q_df.replace(to_replace ="\[.", value = '', regex = True)
    q_df=q_df.replace(to_replace ="'", value = '', regex = True)
    q_df=q_df.replace(to_replace =" ", value = '', regex = True)
    q_df=q_df.replace(to_replace ='\]', value = '', regex = True)
    
    d_cosines = []
    
    query_vector = gen_vector_T(q_df['q_clean'])
    query_vector = query_vector.reshape((1,-1))

    d_cosines = np.dot(normalize(query_vector),norm_original_c_feat)
    
    list_d_cosines = d_cosines[0].tolist()
    
    out = np.array(list_d_cosines).argsort()[-k:][::-1]

    list_d_cosines.sort()
    a = pd.DataFrame()
    for i in out:
        a.loc[i,'index'] = str(i)
        a.loc[i,'headline'] = all_original_text_and_headline_news_df['หัวข้อข่าวอ้างอิงของ ทุกแหล่งข่าว'][i]

    list_d_cosines.sort(reverse=True)
    
    for j in range(k):
        a.loc[out[j],'Score'] = list_d_cosines[j]
        
    return a

In [37]:
query = "กรุงเทพธุรกิจ covld-19จีน' เปิดตัววัคซีนโควิด-19'สูดเข้าปอด' ครั้งแรกของโลกแบบ"

In [38]:
%time all_result = cosine_similarity_T(30, query)

Wall time: 101 ms


In [39]:
all_result

index                                           headline     Score
1067  1067  ไวรัสโคโรนา : สหรัฐฯ เริ่มทดสอบวัคซีนโควิด-19 ...  0.328382
859    859  ครั้งแรกของโลก! ปลูกถ่ายสเต็มเซลล์เร่งด่วนจากผ...  0.261137
831    831  อินเดียเล็งเปิดตัว "วัคซีน COVID-19" ตัวแรก 15...  0.238765
2730  2730  ข่าวปลอม อย่าแชร์! รพ.กรุงเทพ เปิดลงทะเบียนจอง...  0.215600
4834  4834  ชัวร์ก่อนแชร์ : ไปสูดโอโซนเพื่อสุขภาพกันเถอะ…จ...  0.198149
520    520      "อังกฤษ" อนุมัติวัคซีน COVID-19 ชาติแรกของโลก  0.192907
2951  2951  ข่าวปลอม อย่าแชร์! ประเทศไทยมีผู้ติดเชื้อโควิด...  0.192509
2320  2320  วัคซีนโควิด-19 จำนวน 2 แสนโดสจากจีน ส่งถึงไทยภ...  0.187361
2961  2961  ข่าวปลอม อย่าแชร์! โรงพยาบาลกรุงเทพเปิดให้ลงทะ...  0.181627
3986  3986             ชัวร์ก่อนแชร์ : 2559 ข่าวปลอม ป่วนโลก?  0.181374
1319  1319  ข่าวปลอม อย่าแชร์! ล่าสุดกรุงเทพติดเชื้อไวรัสโ...  0.178739
3576  3576  วัคซีนไข้หวัดใหญ่ สามารถฉีดวันเดียวกับวัคซีนโค...  0.171330
5121  5121  ชัวร์ก่อนแชร์ FACTSHEET : อาการปอดอักเสบจากโรค...  0.163820
2294  2294  ข่าวปลอม อย่าแชร์! คลิปจากต่างประเทศแนะดื่มน้ำ...  0.160953
3041  3041  ข่าวปลอม อย่าแชร์! คลิปจากต่างประเทศแนะดื่มน้ำ...  0.160953
3083  3083  เปิดลงทะเบียนฉีดวัคซีนโควิด-19 สำหรับผู้ประกอบ...  0.160755
2891  2891  ข่าวปลอม อย่าแชร์! ต้มน้ำสมุนไพร และใช้ผ้าคลุม...  0.159329
5539  5539  ชัวร์ก่อนแชร์ LIVE : 25 ส.ค. 64 สมุนไพรจีน กับ...  0.157690
1088  1088  ลุ้นข่าวดี เผยโฉม "วัคซีนโควิด-19" จีนไฟเขียวท...  0.157382
3667  3667  ข่าวปลอม อย่าแชร์! ธ.ออมสิน เปิดตัวสินเชื่อไทร...  0.157135
2781  2781  ข่าวบิดเบือน นักศึกษาไทยกลับไปเรียนที่จีนไม่ได...  0.155516
568    568  ด่วน ศบค.รายงาน พบผู้ติดเชื้อรายใหม่ 4 ราย พบ ...  0.154248
6        6  โลกกำลังตาย! นักวิทยาศาสตร์เตือน "แกนกลางโลก" ...  0.149522
2613  2613  ข่าวปลอม อย่าแชร์! ผลิตภัณฑ์ Austamin AVEO ช่ว...  0.149383
4404  4404  ชัวร์ก่อนแชร์ : ประเทศไทยน้ำมันแพงที่สุดในโลก ...  0.148166
3360  3360  ข่าวปลอม อย่าแชร์! เอกสารจากธปท. ชักชวนประชาชน...  0.147125
914    914  เซี่ยงไฮ้ทดลองแอนติบอดีสกัด COVID-19 โดยตรงในม...  0.146536
1041  1041  ม.อ.เปิดตัวชุดตรวจคัดกรองการติดเชื้อไวรัสก่อโร...  0.144997
597    597  สมัครเรียนออนไลน์ แต่ถูกนำชื่อไปสมัครธุรกิจขายตรง  0.144089
2476  2476  ข่าวปลอม อย่าแชร์! ฉีดวัคซีนปอดอักเสบ สามารถป้...  0.140791

In [40]:
all_result_with_url = pd.DataFrame()
for i in range(len(all_result)):
    if float(all_result.iloc[i]["Score"]) != 0.0:
        all_result_with_url.loc[i,'index'] = all_result.iloc[i]["index"]
        all_result_with_url.loc[i,'headline'] = all_result.iloc[i]["headline"]
        all_result_with_url.loc[i,'url'] = all_original_text_and_headline_news_df["URL ของ ทุกแหล่งข่าว"][int(all_result.iloc[i]["index"])]
        all_result_with_url.loc[i,'content'] = all_original_text_and_headline_news_df["เนื้อหาข่าวอ้างอิงของ ทุกแหล่งข่าว"][int(all_result.iloc[i]["index"])]
        all_result_with_url.loc[i,'datetime'] = all_original_text_and_headline_news_df["เวลาที่เผยแพร่ข่าวของ ทุกแหล่งข่าว"][int(all_result.iloc[i]["index"])]
        all_result_with_url.loc[i,'domain'] = all_original_text_and_headline_news_df["domain เจ้าของข่าว ทุกแหล่งข่าว"][int(all_result.iloc[i]["index"])]

In [41]:
#append user input เข้าไปใน all_result_with_url ด้วย
query_df = {'index': '-1', 'headline': query, 'url': '', 'content': ''}
all_result_with_url = all_result_with_url.append(query_df, ignore_index = True)
    
js = all_result_with_url.to_dict('records')

In [42]:
all_result_with_url

index                                           headline  \
0   1067  ไวรัสโคโรนา : สหรัฐฯ เริ่มทดสอบวัคซีนโควิด-19 ...   
1    859  ครั้งแรกของโลก! ปลูกถ่ายสเต็มเซลล์เร่งด่วนจากผ...   
2    831  อินเดียเล็งเปิดตัว "วัคซีน COVID-19" ตัวแรก 15...   
3   2730  ข่าวปลอม อย่าแชร์! รพ.กรุงเทพ เปิดลงทะเบียนจอง...   
4   4834  ชัวร์ก่อนแชร์ : ไปสูดโอโซนเพื่อสุขภาพกันเถอะ…จ...   
5    520      "อังกฤษ" อนุมัติวัคซีน COVID-19 ชาติแรกของโลก   
6   2951  ข่าวปลอม อย่าแชร์! ประเทศไทยมีผู้ติดเชื้อโควิด...   
7   2320  วัคซีนโควิด-19 จำนวน 2 แสนโดสจากจีน ส่งถึงไทยภ...   
8   2961  ข่าวปลอม อย่าแชร์! โรงพยาบาลกรุงเทพเปิดให้ลงทะ...   
9   3986             ชัวร์ก่อนแชร์ : 2559 ข่าวปลอม ป่วนโลก?   
10  1319  ข่าวปลอม อย่าแชร์! ล่าสุดกรุงเทพติดเชื้อไวรัสโ...   
11  3576  วัคซีนไข้หวัดใหญ่ สามารถฉีดวันเดียวกับวัคซีนโค...   
12  5121  ชัวร์ก่อนแชร์ FACTSHEET : อาการปอดอักเสบจากโรค...   
13  2294  ข่าวปลอม อย่าแชร์! คลิปจากต่างประเทศแนะดื่มน้ำ...   
14  3041  ข่าวปลอม อย่าแชร์! คลิปจากต่างประเทศแนะดื่มน้ำ...   
15  3083  เปิดลงทะเบียนฉีดวัคซีนโควิด-19 สำหรับผู้ประกอบ...   
16  2891  ข่าวปลอม อย่าแชร์! ต้มน้ำสมุนไพร และใช้ผ้าคลุม...   
17  5539  ชัวร์ก่อนแชร์ LIVE : 25 ส.ค. 64 สมุนไพรจีน กับ...   
18  1088  ลุ้นข่าวดี เผยโฉม "วัคซีนโควิด-19" จีนไฟเขียวท...   
19  3667  ข่าวปลอม อย่าแชร์! ธ.ออมสิน เปิดตัวสินเชื่อไทร...   
20  2781  ข่าวบิดเบือน นักศึกษาไทยกลับไปเรียนที่จีนไม่ได...   
21   568  ด่วน ศบค.รายงาน พบผู้ติดเชื้อรายใหม่ 4 ราย พบ ...   
22     6  โลกกำลังตาย! นักวิทยาศาสตร์เตือน "แกนกลางโลก" ...   
23  2613  ข่าวปลอม อย่าแชร์! ผลิตภัณฑ์ Austamin AVEO ช่ว...   
24  4404  ชัวร์ก่อนแชร์ : ประเทศไทยน้ำมันแพงที่สุดในโลก ...   
25  3360  ข่าวปลอม อย่าแชร์! เอกสารจากธปท. ชักชวนประชาชน...   
26   914  เซี่ยงไฮ้ทดลองแอนติบอดีสกัด COVID-19 โดยตรงในม...   
27  1041  ม.อ.เปิดตัวชุดตรวจคัดกรองการติดเชื้อไวรัสก่อโร...   
28   597  สมัครเรียนออนไลน์ แต่ถูกนำชื่อไปสมัครธุรกิจขายตรง   
29  2476  ข่าวปลอม อย่าแชร์! ฉีดวัคซีนปอดอักเสบ สามารถป้...   
30    -1  กรุงเทพธุรกิจ covld-19จีน' เปิดตัววัคซีนโควิด-...   

                                                  url  \
0     https://www.bbc.com/thai/international-51925767   
1           https://news.thaipbs.or.th/content/293953   
2           https://news.thaipbs.or.th/content/294277   
3   https://www.antifakenewscenter.com/news/activi...   
4                     https://tna.mcot.net/tna-331110   
5           https://news.thaipbs.or.th/content/298859   
6   https://www.antifakenewscenter.com/news/activi...   
7   https://www.antifakenewscenter.com/news/activi...   
8   https://www.antifakenewscenter.com/news/activi...   
9                      https://tna.mcot.net/tna-91549   
10  https://www.antifakenewscenter.com/news/activi...   
11  https://www.antifakenewscenter.com/news/activi...   
12                    https://tna.mcot.net/tna-434584   
13  https://www.antifakenewscenter.com/news/activi...   
14  https://www.antifakenewscenter.com/news/activi...   
15  https://www.antifakenewscenter.com/news/activi...   
16  https://www.antifakenewscenter.com/news/activi...   
17           https://tna.mcot.net/sureandshare-765544   
18    https://www.komchadluek.net/news/foreign/427355   
19  https://www.antifakenewscenter.com/news/activi...   
20  https://www.antifakenewscenter.com/news/activi...   
21   https://www.komchadluek.net/news/regional/448556   
22  https://mgronline.com/around/detail/9650000007354   
23  https://www.antifakenewscenter.com/news/activi...   
24                    https://tna.mcot.net/tna-210081   
25  https://www.antifakenewscenter.com/news/activi...   
26          https://news.thaipbs.or.th/content/293398   
27   https://mgronline.com/south/detail/9630000044393   
28          https://news.thaipbs.or.th/content/297858   
29  https://www.antifakenewscenter.com/news/activi...   
30                                                      

                                              content  \
0   17 มีนาคม 2020ที่มาของภาพ  สถาบันสุขภาพแห่งชาต...   
1   หมอรามาธิบดี ประสบความความสำเร็จ ปลูกถ่ายสเ

---------------------------------------

In [43]:
all_result_with_url.to_csv("C:/Users/Administrator/Desktop/all_result_with_url.csv")